In [27]:
import pandas as pd
import numpy as np


pd.set_option('display.max_columns', 10000)

In [28]:
df=pd.read_csv('judge-1377884607_tweet_product_company.csv',encoding = 'unicode_escape')

In [29]:
df.head()

tweet_text  \
0  .@wesley83 I have a 3G iPhone. After 3 hrs twe...   
1  @jessedee Know about @fludapp ? Awesome iPad/i...   
2  @swonderlin Can not wait for #iPad 2 also. The...   
3  @sxsw I hope this year's festival isn't as cra...   
4  @sxtxstate great stuff on Fri #SXSW: Marissa M...   

  emotion_in_tweet_is_directed_at  \
0                          iPhone   
1              iPad or iPhone App   
2                            iPad   
3              iPad or iPhone App   
4                          Google   

  is_there_an_emotion_directed_at_a_brand_or_product  
0                                   Negative emotion  
1                                   Positive emotion  
2                                   Positive emotion  
3                                   Negative emotion  
4                                   Positive emotion

In [30]:
df.emotion_in_tweet_is_directed_at.value_counts()

iPad                               946
Apple                              661
iPad or iPhone App                 470
Google                             430
iPhone                             297
Other Google product or service    293
Android App                         81
Android                             78
Other Apple product or service      35
Name: emotion_in_tweet_is_directed_at, dtype: int64

In [31]:
df.is_there_an_emotion_directed_at_a_brand_or_product.value_counts()

No emotion toward brand or product    5389
Positive emotion                      2978
Negative emotion                       570
I can't tell                           156
Name: is_there_an_emotion_directed_at_a_brand_or_product, dtype: int64

In [32]:
df.is_there_an_emotion_directed_at_a_brand_or_product.isna().sum()

0

In [33]:
df.emotion_in_tweet_is_directed_at.isna().sum()

5802

In [34]:
df.shape

(9093, 3)

In [35]:
df.columns=['tweet','company','emotion']

In [36]:
df=df.drop([6]).reset_index(drop=True)

In [37]:
df[df.emotion=='I can\'t tell'].emotion="No emotion toward brand or product"

/Users/carlosruiz/opt/anaconda3/lib/python3.7/site-packages/pandas/core/generic.py:5303: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value


In [38]:
df.emotion.value_counts()

No emotion toward brand or product    5388
Positive emotion                      2978
Negative emotion                       570
I can't tell                           156
Name: emotion, dtype: int64

In [39]:
df['emotion'] = df['emotion'].apply(lambda x: "No emotion toward brand or product" if x == "I can't tell" else x)

In [40]:
df['emotion'].value_counts()

No emotion toward brand or product    5544
Positive emotion                      2978
Negative emotion                       570
Name: emotion, dtype: int64

In [41]:
df.tweet.dropna(inplace=True)

In [42]:
df[df.company.isna()].head()

tweet company  \
5   @teachntech00 New iPad Apps For #SpeechTherapy...     NaN   
15  Holler Gram for iPad on the iTunes App Store -...     NaN   
31  Attn: All  #SXSW frineds, @mention Register fo...     NaN   
32      Anyone at  #sxsw want to sell their old iPad?     NaN   
33  Anyone at  #SXSW who bought the new iPad want ...     NaN   

                               emotion  
5   No emotion toward brand or product  
15  No emotion toward brand or product  
31  No emotion toward brand or product  
32  No emotion toward brand or product  
33  No emotion toward brand or product

In [43]:
df[df.emotion=='No emotion toward brand or product'].company.value_counts()

iPad                               28
Apple                              23
Google                             16
Other Google product or service    10
iPad or iPhone App                 10
iPhone                             10
Android                             1
Android App                         1
Other Apple product or service      1
Name: company, dtype: int64

In [44]:
df[df.emotion=='No emotion toward brand or product'].company.isna().sum()

5444

In [45]:
punctuation=[",",".","#","!","@","$","?","$","%","&","-","_"]
apple=['iPhone',"iPad&quot;","iphone ",'i Pad','i Pad',"Apple.","iPad?","#iPad","#iPhone",'iPad','Mac',"iphone,",'iPod','ipod','ipad','mac','Apple','apple','Apple\'s','apple\'s',"#Apple",'#apple','I-Pad']
google=['Google','google','android','Android','Google.','android,',"#android",'Google\'s','google\'s','googles' ,'#google','#Google']

In [46]:
for index in df.index:
    tweet="".join(i if i not in punctuation else " " for i in df.tweet[index])
    condition=0
    if bool(set(tweet.split())&set(apple))==True:
        df.company[index]=(list(set(tweet.split())&set(apple))[0].title().strip('\'s')).strip('\'S')
        condition=1
    else:
        condition=0
        
    if (bool(set(tweet.split())&set(google))==True) and condition==0:
        df.company[index]=(list(set(tweet.split())&set(google))[0].title().strip('\'s')).strip('\'S')
        
    elif (bool(set(tweet.split())&set(google))==True) and condition==1:
        df.company[index]+= " & "+(list(set(tweet.split())&set(google))[0].title().strip('\'s')).strip('\'S')

In [48]:
df['company'] = df['company'].apply(lambda x: "iPad" if x == "Ipad" else x)
df['company'] = df['company'].apply(lambda x: "iPhone" if x == "Iphone" else x)

In [49]:
df.company.value_counts()

Google                             2318
iPad                               2263
Apple                              1611
iPhone                             1128
Android                             374
Iphone & Android                    113
iPad or iPhone App                   71
Ipad & Android                       28
Apple & Google                       22
Mac                                  21
Other Apple product or service       12
Other Google product or service      11
Apple & Android                       6
Ipad & Google                         5
Iphone & Google                       2
Mac & Android                         1
Ipod                                  1
Name: company, dtype: int64

In [50]:
df[['company','emotion','tweet']].groupby(['company','emotion']).count()

tweet
company                         emotion                                  
Android                         Negative emotion                       18
                                No emotion toward brand or product    209
                                Positive emotion                      147
Apple                           Negative emotion                       94
                                No emotion toward brand or product    884
                                Positive emotion                      633
Apple & Android                 No emotion toward brand or product      3
                                Positive emotion                        3
Apple & Google                  No emotion toward brand or product     14
                                Positive emotion                        8
Google                          Negative emotion                      131
                                No emotion toward brand or product   1527
                                Positive emotion                      660
Ipad & Android                  No emotion toward brand or product     24
                                Positive emotion                        4
Ipad & Google                   No emotion toward brand or product      3
                                Positive emotion                        2
Iphone & Android                Negative emotion                        4
                                No emotion toward brand or product     78
                                Positive emotion                       31
Iphone & Google                 No emotion toward brand or product      1
                                Positive emotion                        1
Ipod                            Positive emotion                        1
Mac                             Negative emotion                        1
                                No emotion toward brand or product     11
                                Positive emotion                        9
Mac & Android                   Positive emotion                        1
Other Apple product or service  Positive emotion                       12
Other Google product or service Negative emotion                        3
                                Positive emotion                        8
iPad                            Negative emotion                      172
                                No emotion toward brand or product   1131
                                Positive emotion                      960
iPad or iPhone App              Negative emotion                        7
                                No emotion toward brand or product      1
                                Positive emotion                       63
iPhone                          Negative emotion                      134
                                No emotion toward brand or product    591
                                Positive emotion                      403

In [186]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords 
from nltk.tokenize import RegexpTokenizer

stopwords = ['am','he','i','the','hi']

vectorizer = TfidfVectorizer(ngram_range=(1,1),stop_words=stopwords, token_pattern=(r'[a-zA-Z]+'))

text_tf = vectorizer.fit_transform(df['tweet'])
text_tf.data

array([0.0374645 , 0.33747004, 0.31835115, ..., 0.18673341, 0.08103873,
       0.17591468])

In [187]:
text_tf

<9092x9290 sparse matrix of type '<class 'numpy.float64'>'
	with 147671 stored elements in Compressed Sparse Row format>

In [188]:
pd.DataFrame(text_tf)

0
0       (0, 7948)\t0.03746450253941902\n  (0, 7701)\...
1       (0, 8484)\t0.33544761145124324\n  (0, 3136)\...
2       (0, 2333)\t0.29598725319385377\n  (0, 8193)\...
3       (0, 1805)\t0.38487769745195866\n  (0, 449)\t...
4       (0, 9115)\t0.28707033395978776\n  (0, 5312)\...
...                                                 ...
9087    (0, 2700)\t0.9118040538367157\n  (0, 4701)\t...
9088    (0, 790)\t0.24457556672273711\n  (0, 6335)\t...
9089    (0, 5675)\t0.28434015327589474\n  (0, 2881)\...
9090    (0, 9232)\t0.33696382051871293\n  (0, 1565)\...
9091    (0, 8154)\t0.611262256496504\n  (0, 5609)\t0...

[9092 rows x 1 columns]

In [189]:
df = pd.DataFrame(text_tf.todense(),columns = vectorizer.get_feature_names())
df

a  aapl  aaron  aarpbulletin   ab  abacus  abandoned  abba  abc  \
0     0.093697   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
1     0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
2     0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
3     0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
4     0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
...        ...   ...    ...           ...  ...     ...        ...   ...  ...   
9087  0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
9088  0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
9089  0.075548   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
9090  0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   
9091  0.000000   0.0    0.0           0.0  0.0     0.0        0.0   0.0  0.0   

      aber  abilities  ability  able  abnormal  abound     about  above  \
0      0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
1      0.0        0.0      0.0   0.0       0.0     0.0  0.154744    0.0   
2      0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
3      0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
4      0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
...    ...        ...      ...   ...       ...     ...       ...    ...   
9087   0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
9088   0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
9089   0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
9090   0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   
9091   0.0        0.0      0.0   0.0       0.0     0.0  0.000000    0.0   

      abroad  absolute  absolutely  absolutley  abt  abuzz  academy  acc  \
0        0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
1        0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
2        0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
3        0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
4        0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
...      ...       ...         ...         ...  ...    ...      ...  ...   
9087     0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
9088     0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
9089     0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
9090     0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   
9091     0.0       0.0         0.0         0.0  0.0    0.0      0.0  0.0   

      accelerater  acceleration  accelerator  accept  acceptable  access  \
0             0.0           0.0          0.0     0.0         0.0     0.0   
1             0.0           0.0          0.0     0.0         0.0     0.0   
2             0.0           0.0          0.0     0.0         0.0     0.0   
3             0.0           0.0          0.0     0.0         0.0     0.0   
4             0.0           0.0          0.0     0.0         0.0     0.0   
...           ...           ...          ...     ...         ...     ...   
9087          0.0           0.0          0.0     0.0         0.0     0.0   
9088          0.0           0.0          0.0     0.0         0.0     0.0   
9089          0.0           0.0          0.0     0.0         0.0     0.0   
9090          0.0           0.0          0.0     0.0         0.0     0.0   
9091          0.0           0.0          0.0     0.0         0.0     0.0   

      accessibility  accessible  accessories  accessory  accesssxsw  \
0               0.0         0.0          0.0        0.0         0.0   
1               0.0         0.0          0.0        0.0         0.0   
2               0.0         0.0          0.0        0.0         0.0   
3               0.0         0.0          